In [4]:


import sys
sys.executable

'/home/goonieb/anaconda2/bin/python'

In [5]:
import os
import json
import pymongo
import musicbrainzngs
import arrow
from datetime import datetime
from pymongo import MongoClient
from collections import defaultdict
from dateutil import parser
import pickle


In [6]:
# setup mongo
client = MongoClient()
db = client["bandstour"]
bandsintown =  db["bandsintown"]



#setup mbrainz client
musicbrainzngs.set_useragent("Example music app", "0.1", "http://example.com/music")

# source data
DATA_FOLDER = "data/labels"
countMBID = 0
countNAME = 0
count = 0
# date parsing
DATETIME_FORMAT = '%Y-%m-%dT%H:%M:%S'
DATETIME_FORMAT_FOR_MSBNZ ='%Y-%m-%d'
# init label_db_retrieval
labels_aliases ={}
#retrieve label for each artist before a tour starts
#i.e what is the album previously to the first year
for artist in db.minedArtists.find() :
                    print artist["name"]
    
                    #print db.minedArtists[artist]
                    #print artist
                    labels_dict= defaultdict(list)
                    labels_dict["id"]=[]

                    if  artist["mbid"] is ( None ) :
                        print ("NOMBID for",artist["name"])

                    else:
                     if  bool(artist["mbid"]) is ( False ) :
                      print ("NOMBID2 for",artist["name"])

                     else:
                      print "aartist_mbid", artist["mbid"]
                     if os.path.exists("./release_mbnz/"+artist["name"]+artist["mbid"]+".obj")==True:
                      with open("./release_mbnz/"+artist["name"]+artist["mbid"]+".obj", 'rb') as handle:
                        artist["releases"]= pickle.load(handle)
                     else:
                      try:
                        artist["releases"]=(musicbrainzngs.browse_releases( artist["mbid"], release_type=["album"], includes=["labels"] ))
                        try:
                            with open("./release_mbnz/"+artist["name"]+artist["mbid"]+".obj", 'wb') as handle:
                                pickle.dump(artist["releases"], handle, protocol=pickle.HIGHEST_PROTOCOL)    
                        except:
                            pass
                        #print "...."
                        #print artist["release_groups"]
                        key= 0
                        for release in  artist["releases"]["release-list"]:
                            #print release
                            if  release.has_key("release-event-list"):
                                #print "artist_name:",artist["name"]
                                #print "albumtitle:",release["title"]
                                #print "albumid:",release["id"]
                                #print "label-list",release["label-info-list"]
                                #print "releaseLBL",release["label-info-list"]
                                if not release["label-info-list"]:
                                    print "pppppppppppppp"
                                
                                else:
                                 if release["label-info-list"][0].has_key('label'):
                                  for label in release["label-info-list"]:
                                    #WE NEED TO TEST HERE
                                    #print "label:",label["label"]["sort-name"]
                                    #print "labelid:",label
                                    
#WE CREATE A DICTIONNARY WITH OUR FIELDS, WITH FORMAT
                                    if label.has_key('label'):
                                     if label["label"]["id"] not in labels_dict["labids"]:
                                        labels_dict["labids"].append(label["label"]["id"])
                                        labels_dict[label["label"]["id"]]={}

                                        labels_dict[label["label"]["id"]]["label_name"]=label["label"]["sort-name"]
                                        labels_dict[label["label"]["id"]]["label_id" ]=label["label"]["id"]
#WE Build the label aliases tables here so that all labels have their relationships##
                                        if label["label"]["id"] not in labels_aliases:
                                            labels_aliases[label["label"]["id"]] = musicbrainzngs.get_label_by_id(label["label"]["id"], includes=["aliases", "annotation", "area-rels", "label-rels", "place-rels"])
                                        #print "labels_aliases",labels_aliases
                                     labels_dict[label["label"]["id"]][str(key)]={}
                                    #print key
                                     labels_dict[label["label"]["id"]][str(key)]["album_id"]=release["id"]
                                     labels_dict[label["label"]["id"]][str(key)]["album_title"]=release["title"]
                                     releDate=release["release-event-list"][0]
                                #print "releDate", release["release-event-list"][0]
                                     if  releDate.has_key("date"):
                                        dateRel=arrow.get(releDate["date"])
                                        #print "date:", dateRel.strftime('%Y-%m-%d')
                                        labels_dict[label["label"]["id"]][str(key)]["album_date"]=dateRel.strftime('%Y-%m-%d')
                                     key = key +1
                                 else:
                                    print "NORELEASEDATE2"
                                    #key = key +1
                            #else:
                                #key = key +1
                                #print "NORELEASEDATE"
#NOW we make a nice lightweight object to push to mongo
                        labels_dict["name"]=artist["name"]
                        print labels_dict["name"],'\r\n'
                        db.labels_dict_per_artist.update({'myid': artist["name"] } ,labels_dict, upsert=True, multi=False)
                      except  musicbrainzngs.ResponseError:
                        print "oups",artist["name"]

                #with open(os.path.join(DATA_FOLDER,artist["name"],".json"), 'w') as outfile:
                             #   json.dump(labels_dict, outfile)
                            #db.minedArtists.artist.insert_one(labels_dict)
#with open(os.path.join(DATA_FOLDER,"label_equiv_table.json"), 'w') as outfile:
 #                               json.dump(labels_aliases, outfile)
#print labels_aliases,'\r\n\r\n\r\n'
import pickle



with open('labels_aliases.obj', 'wb') as handle:
    pickle.dump(labels_aliases, handle, protocol=pickle.HIGHEST_PROTOCOL)



조수미
aartist_mbid dd21a142-cf44-4e22-add6-a50eea696854
Лили Иванова
aartist_mbid ab634a19-20e3-4801-975e-a230f899af8a
ᵀᴴᴱ ᴼᴿᴵᴳᴵᴻᴬᴸ Funky Monkey
('NOMBID for', u'\u1d40\u1d34\u1d31 \u1d3c\u1d3f\u1d35\u1d33\u1d35\u1d3b\u1d2c\u1d38 Funky Monkey')
Калевала
('NOMBID for', u'\u041a\u0430\u043b\u0435\u0432\u0430\u043b\u0430')
Кристина Орбакайте
aartist_mbid e71738bd-39d4-4699-b6c2-688f95b31732
Дмитрий Дмитриевич Шостакович
aartist_mbid 519dd32e-8f30-4380-8826-7aa99169e1bb
Валерия
aartist_mbid b4313680-2f57-4ec6-87a7-24873133ba4c
Евгений Игоревич Кисин
aartist_mbid 5761282a-0965-4ff6-9796-7b9ba0ed70e2
Би-2
aartist_mbid 5ca35ace-4006-4d4a-af04-5cd91dafab14
Анна Юрьевна Нетребко
aartist_mbid 90cba256-80b2-464f-9d58-a877a3757d3a
Μελίνα Ασλανίδου
aartist_mbid d55702f8-1b33-494e-8c9c-e6fd948bbee8
ŚexPistols Eẋperience
('NOMBID for', u'\u015aexPistols E\u1e8bperience')
ÜBERMENSCH (Rammstein Tribute Band)
('NOMBID for', u'\xdcBERMENSCH (Rammstein Tribute Band)')
Ørsted
('NOMBID for', u'\xd8rsted')
Øka

truett
('NOMBID for', u'truett')
transient
aartist_mbid 4cb5b170-07f9-4428-bdfa-7b74a2122553
tori kelly
('NOMBID for', u'tori kelly')
tobyMac
aartist_mbid 8484e4ab-b6b5-4326-b837-72eb72c9e8a4
tim gearan
('NOMBID for', u'tim gearan')
theo kottis
('NOMBID for', u'theo kottis')
theSHIFT
('NOMBID for', u'theSHIFT')
the vaughns
('NOMBID for', u'the vaughns')
the the Band Band
('NOMBID for', u'the the Band Band')
the peptides
('NOMBID for', u'the peptides')
the magician
('NOMBID for', u'the magician')
the Workshy
('NOMBID for', u'the Workshy')
the Whooligan
('NOMBID for', u'the Whooligan')
the Way Up
('NOMBID for', u'the Way Up')
the ThoughtCriminals
('NOMBID for', u'the ThoughtCriminals')
the Tea Club
('NOMBID for', u'the Tea Club')
the Stuntmen
('NOMBID for', u'the Stuntmen')
the Stampede
('NOMBID for', u'the Stampede')
the Sour Notes
('NOMBID for', u'the Sour Notes')
the Snips
('NOMBID for', u'the Snips')
the Sleeper
('NOMBID for', u'the Sleeper')
the Ruination
('NOMBID for', u'the Ruinat

oups yellowtieguy
xxyyxx
('NOMBID for', u'xxyyxx')
www.kierangoss.com
('NOMBID for', u'www.kierangoss.com')
wonder woman
('NOMBID for', u'wonder woman')
william becket
('NOMBID for', u'william becket')
whetherman
('NOMBID for', u'whetherman')
wax wings
('NOMBID for', u'wax wings')
w/Billy Masters on guitar
('NOMBID for', u'w/Billy Masters on guitar')
w/ This Or The Apocalypse, Ice Nine Kills
('NOMBID for', u'w/ This Or The Apocalypse, Ice Nine Kills')
w/ For Today, The Word Alive, Memphis May Fire, and Upon A Burning Body  
('NOMBID for', u'w/ For Today, The Word Alive, Memphis May Fire, and Upon A Burning Body  ')
vverevvolf
('NOMBID for', u'vverevvolf')
viech
('NOMBID for', u'viech')
uvm.
('NOMBID for', u'uvm.')
tyler boone
('NOMBID for', u'tyler boone')
trp
('NOMBID for', u'trp')
theSurrendering
('NOMBID for', u'theSurrendering')
the kats
('NOMBID for', u'the kats')
the come up
('NOMBID for', u'the come up')
the black sound
('NOMBID for', u'the black sound')
the World's Hottest '80s

oups many
mafia rusa
('NOMBID for', u'mafia rusa')
lucent dossier
('NOMBID for', u'lucent dossier')
litz 
('NOMBID for', u'litz ')
linnie & amy joy
('NOMBID for', u'linnie & amy joy')
lilabungalow
('NOMBID for', u'lilabungalow')
laCasta
('NOMBID for', u'laCasta')
la Rappresentante di Lista
('NOMBID for', u'la Rappresentante di Lista')
kojey radical
('NOMBID for', u'kojey radical')
kirk baxley
('NOMBID for', u'kirk baxley')
kachupa
('NOMBID for', u'kachupa')
k.flay
aartist_mbid d1fc999f-6184-41a6-bcb1-7c59bf74a6e1
joe mullins
('NOMBID for', u'joe mullins')
joe fox
('NOMBID for', u'joe fox')
jason philips
('NOMBID for', u'jason philips')
iwrestledabearonce, Oceano, For All Those Sleeping
('NOMBID for', u'iwrestledabearonce, Oceano, For All Those Sleeping')
it's always sunny in tijuana
('NOMBID for', u"it's always sunny in tijuana")
ici et lui
('NOMBID for', u'ici et lui')
iAROSS
('NOMBID for', u'iAROSS')
honey mustard
('NOMBID for', u'honey mustard')
hold youth
('NOMBID for', u'hold yout

Zane Lowe
aartist_mbid 60c693ce-2121-47c5-bc20-975e43137e48
Zander DJ
('NOMBID for', u'Zander DJ')
Zakk Wylde
aartist_mbid b109e75a-89d9-4fb2-843c-c0418b755d4c
Zak Downtown
('NOMBID for', u'Zak Downtown')
Zahi
('NOMBID for', u'Zahi')
Zack Walther Band
('NOMBID for', u'Zack Walther Band')
Zack Shornick and The Pathetic Men
('NOMBID for', u'Zack Shornick and The Pathetic Men')
Zack Joseph
('NOMBID for', u'Zack Joseph')
Zach Williams
('NOMBID for', u'Zach Williams')
Zach Seabaugh
('NOMBID for', u'Zach Seabaugh')
Zach Pohl
('NOMBID for', u'Zach Pohl')
Zach Moore
('NOMBID for', u'Zach Moore')
Zach
aartist_mbid 3ff3dbbb-dbf1-458f-a8fd-79206f824cb7
ZUCKERWATT
('NOMBID for', u'ZUCKERWATT')
ZOVIET
('NOMBID for', u'ZOVIET')
ZIZE Dupanier
('NOMBID for', u'ZIZE Dupanier')
ZILLAS ON ACID
('NOMBID for', u'ZILLAS ON ACID')
ZESRS
('NOMBID for', u'ZESRS')
ZAJO
('NOMBID for', u'ZAJO')
Z-Trip
aartist_mbid 03f93de6-6d62-4710-bcc7-9b3d7c3d95f5
Yächtley Crëw
('NOMBID for', u'Y\xe4chtley Cr\xebw')
Yvonne Cat

Zanarelli
('NOMBID for', u'Zanarelli')
Zalon
('NOMBID for', u'Zalon')
Zakir Hussain
aartist_mbid a198b33b-a907-462d-a437-b6cc1b98b8f7
Zak Fennie
('NOMBID for', u'Zak Fennie')
Zaho
aartist_mbid 463814cb-001d-4950-98d2-8822ff765906
Zafakon
('NOMBID for', u'Zafakon')
Zackey Force Funk
('NOMBID for', u'Zackey Force Funk')
Zach Winters Music
('NOMBID for', u'Zach Winters Music')
Zach Torres
('NOMBID for', u'Zach Torres')
Zach Sherwin
('NOMBID for', u'Zach Sherwin')
Zach Quinn
('NOMBID for', u'Zach Quinn')
Zach Person
('NOMBID for', u'Zach Person')
Zach Longoria Project
('NOMBID for', u'Zach Longoria Project')
Zach Johnson Music
('NOMBID for', u'Zach Johnson Music')
Zach Emery
('NOMBID for', u'Zach Emery')
Zach Djanikian
('NOMBID for', u'Zach Djanikian')
Zacarias Ferreira
aartist_mbid e19a81b2-3824-464c-8635-7f4082dad10f
Zac Harmon
aartist_mbid 08e88d17-28eb-4aaa-a05c-9d6dd6f17c68
ZZ Ward
('NOMBID for', u'ZZ Ward')
ZRIKU
('NOMBID for', u'ZRIKU')
ZOYA
('NOMBID for', u'ZOYA')
ZOB'
('NOMBID for

Wild Ones
aartist_mbid b66f7751-64fb-43d0-9cbb-f313cb52a6b6
Wild Arms
('NOMBID for', u'Wild Arms')
Wil Kinky
('NOMBID for', u'Wil Kinky')
Wil Anderson
('NOMBID for', u'Wil Anderson')
Wig Party
('NOMBID for', u'Wig Party')
Wife
('NOMBID for', u'Wife')
Wiener Sängerknaben
aartist_mbid 7badcc14-8d16-4734-acda-40645d156602
Widower
aartist_mbid e27a8c9e-6090-49a7-b7ff-746d935eb729
Widow
aartist_mbid 9ff56bac-81f7-4114-b971-58ff431cfb4d
Youngsta
aartist_mbid df7bb489-3f43-4405-95b9-7dd2bb31072f
Younger
('NOMBID for', u'Younger')
Youngblood
('NOMBID for', u'Youngblood')
Young the Giant
('NOMBID for', u'Young the Giant')
Young and Heartless
('NOMBID for', u'Young and Heartless')
Young Widows
aartist_mbid c9e69e05-2c05-4700-a311-53fe4ffc649e
Young Rebel Set
aartist_mbid 7b2aeb3f-c51f-4b35-8f38-54bdbab7a8a9
Young Noah
aartist_mbid c7d3b421-564f-467b-94ef-ad9a1ce80344
Young Medicine
('NOMBID for', u'Young Medicine')
Young Mammals
('NOMBID for', u'Young Mammals')
Young Heirlooms
('NOMBID for', u'Y

KeyboardInterrupt: 

In [7]:
with open("labels_aliases.obj", 'rb') as handle:
                        labels_aliases= pickle.load(handle)

In [9]:
print str(labels_aliases)[:10]

{'781c73fd


In [51]:
#HERE WE PREPARE THE NETWORK

missing_nodes=[]
locker=0
for lab in labels_aliases:
    print "---------------"
    print "mbid: ",lab
    print "nom:",labels_aliases[lab]["label"]["name"]
    
    if  "area" in labels_aliases[lab]["label"]:
        print "localisation:"
        print labels_aliases[lab]["label"]["area"]["name"]
        if 'iso-3166-1-code-list' in labels_aliases[lab]["label"]["area"]:
            print labels_aliases[lab]["label"]["area"]['iso-3166-1-code-list']
        else: 
            if 'iso-3166-2-code-list' in labels_aliases[lab]["label"]["area"]:
                print labels_aliases[lab]["label"]["area"]['iso-3166-2-code-list']
            else:
                print "#############",labels_aliases[lab]["label"]["area"]
                
    if  "life-span" in labels_aliases[lab]["label"]:
        print "dates",labels_aliases[lab]["label"]["life-span"]
    if "label-relation-list" in labels_aliases[lab]["label"]:
        #print "relations", labels_aliases[lab]["label"]["label-relation-list"]
        for relation in labels_aliases[lab]["label"]["label-relation-list"]:
            #print "relation",relation
            locker=0

            if "direction" in relation: 
                if relation["direction"] == 'backward': print "APPARTIENT A"
                else:
                        print relation["direction"]
            else:
                print "EST PROPRIETAIRE DE: "
                locker=1
            print relation['target']
            print relation['label']['name']
            for target, data in labels_aliases.iteritems():
                #print "DATA",data
                #print "TARGET",target
                if target == relation['target'] :
                    print "TROUVE!!!!!!!!!!!! :)"
                    locker=1
                    
            if locker == 0:
                
                print "ABSENT, ON AJOUTE A LA LISTE DES MANQUANTS"
                missing_nodes.append(relation['target'])

                    
                    
                    
print missing_nodes
print "nombre de points manquants: ",len(missing_nodes)
                    



with open('missing_nodes.obj', 'wb') as handle:
    pickle.dump(missing_nodes, handle, protocol=pickle.HIGHEST_PROTOCOL)
        

                 
                

---------------
mbid:  781c73fd-71d0-4309-b9bb-a3036ffc705c
nom: The Spew Records
localisation:
Italy
['IT']
dates {'begin': '2000'}
---------------
mbid:  7020b318-6b95-49d4-ab5f-7cb1fe9fd3ea
nom: N.V. Bovema
localisation:
Netherlands
['NL']
dates {'ended': 'true', 'begin': '1946', 'end': '1971'}
EST PROPRIETAIRE DE: 
7e1a1cff-ffca-440a-9999-3bc7dd0a03fa
EMI-Bovema Holland
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  a7d455f1-93f6-4bb7-a9cf-e4514efd7e02
nom: Ulftone Music
localisation:
Germany
['DE']
---------------
mbid:  c3da866a-1ed0-4d10-96e0-d6b5b80a50a0
nom: Label "X"
localisation:
Australia
['AU']
---------------
mbid:  aa3400d4-26f8-47eb-8bd7-2d71684b7885
nom: Rising Pulse Records
localisation:
Brooklyn
############# {'sort-name': 'Brooklyn', 'id': 'a71b0d32-7752-49e9-8594-2247ad6ac12c', 'name': 'Brooklyn'}
dates {'begin': '2008'}
---------------
mbid:  23f094b1-2d2e-4601-aff6-3b4d294774ca
nom: Age of Panik
localisation:
United Kingdom
['GB']
APPARTIENT A
3daa8f5f-ae92-412f-b7

dates {'ended': 'true', 'begin': '1994'}
---------------
mbid:  0a96f9df-af33-4311-b866-d39e0a5f3485
nom: Surfdog Records
localisation:
United States
['US']
dates {'begin': '1993'}
---------------
mbid:  a587d5cb-9516-439f-b8ba-db5a2824f0c2
nom: Merkton
localisation:
Germany
['DE']
---------------
mbid:  229590d4-0a97-4dae-a40f-c4a1db7e2bfa
nom: פונוקול
localisation:
Israel
['IL']
APPARTIENT A
164be397-9542-4b4a-87cf-c27b7a13b71a
Phonokol Ltd.
TROUVE!!!!!!!!!!!! :)
APPARTIENT A
66ac73bc-672c-4d18-8616-497e29bab6fc
פונודור
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  092246a3-79b9-4793-9899-2a19fd0f9291
nom: YRF Music
localisation:
India
['IN']
---------------
mbid:  7fd6a368-1932-4621-88e1-9a71929ee9b9
nom: Hannibal
localisation:
United States
['US']
dates {'ended': 'true', 'begin': '1980', 'end': '2006-12'}
APPARTIENT A
6dedcd20-3d02-4838-b583-5434eac199d9
Rykodisc
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
e7035bb9-c732-4324-86af-346355bd1085
Carthage Records
---------------
mbid:  

nom: Nettwerk Music Group Inc.
---------------
mbid:  320853c3-4416-43f7-a20e-0afe4a08c1f1
nom: Boo-Hooray
---------------
mbid:  a30ecc21-b0f3-4b13-91fb-a3ab2509955e
nom: Zona Bruta
localisation:
Spain
['ES']
---------------
mbid:  758471c4-3bc8-498d-bdb2-0bb9ea2c9bb1
nom: Perfectly Round Records
localisation:
United States
['US']
---------------
mbid:  b2b2e809-f3c8-46a0-89ab-28a25cbd0311
nom: Ten Point Productions
---------------
mbid:  d36108fb-978c-4787-8db3-b4cb138694eb
nom: Alliance Records
---------------
mbid:  b8b85db4-39fb-417e-87af-12dd878262f8
nom: Unterm Durchschnitt
localisation:
Germany
['DE']
dates {'begin': '1999'}
---------------
mbid:  2e20a9ac-d1bf-4c85-a538-d28572f945e4
nom: 78 PRODUCTIONS
---------------
mbid:  ae9ddfd9-5c54-45f7-88a3-c1af57e2ac93
nom: Smells Like Records
localisation:
United States
['US']
dates {'begin': '1992'}
EST PROPRIETAIRE DE: 
5a980f00-ad17-47ea-bf15-2024beb6335c
Goofin’ Records
---------------
mbid:  874ed90f-1087-430c-8be2-02791ebfbe6e


['GB']
dates {'begin': '2007'}
APPARTIENT A
0253505b-b0f3-4619-8ce0-6a79fe6fbc32
One Little Indian Records
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  43386aae-99df-422e-8fdc-da07a9f88578
nom: Trill Entertainment
---------------
mbid:  d4360e45-ca92-4777-b9c5-891903bbdc6c
nom: Sony Music Entertainment US Latin LLC
localisation:
Miami
############# {'sort-name': 'Miami', 'id': '4a9aeb42-3763-4234-8fb8-1167ac1dfdfe', 'name': 'Miami'}
EST PROPRIETAIRE DE: 
0ca9e520-49f9-4e38-aa59-4afdf55569e9
Sony Discos, Inc.
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
82e029be-2f22-466c-b4b1-ecdac00e6545
Discos 605
EST PROPRIETAIRE DE: 
99962abe-c219-4031-9c6c-c61fc3885944
Sony Music | Latin
TROUVE!!!!!!!!!!!! :)
APPARTIENT A
b54769e4-b75e-4f60-884a-c4714687bb4c
Sony Music Entertainment
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  4add3e83-38b9-43b8-a508-9d51a1aa8ccf
nom: TMD
localisation:
Netherlands
['NL']
---------------
mbid:  c93378a6-87c8-4d75-a1d4-c887ff2cdb4c
nom: Metal Biter
---------------
mb

nom: Mums Records
localisation:
United Kingdom
['GB']
---------------
mbid:  1e99095c-1e9d-48ec-948c-c368f2e57e3b
nom: Cacophonous Records
localisation:
United Kingdom
['GB']
dates {'begin': '1993'}
---------------
mbid:  cacb73b7-6d1b-41ba-aea5-6956ed51757e
nom: BMG Classics
dates {'ended': 'true', 'end': '2005-05-02'}
APPARTIENT A
29d7c88f-5200-4418-a683-5c94ea032e38
BMG
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
456931a9-b2a9-44bd-8aeb-71ca60525a63
Wicklow Records
APPARTIENT A
482a2d73-abe4-4c12-b69c-0e79d6805c10
RCA Gold Seal
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
694c9826-0007-4fab-ad9b-478642e2b70b
Catalyst
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
d49fe768-e91c-404f-9542-3008c4ef9b51
Sony BMG Masterworks
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  ce8222ff-f843-44f6-8af5-eb3ff11f6bae
nom: jazzwerkstatt
---------------
mbid:  129d0c94-8097-4f3b-94a6-cf84ede01c7d
nom: On-U Sound
localisation:
United Kingdom
['GB']
EST PROPRIETAIRE DE: 
ae48d835-0986-413b-b4a6-e50362ff351e

...

dates {'begin': '1951'}
APPARTIENT A
bf2ec6f8-3f38-478a-9d69-0eb082943549
Hungaroton Records
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  a9f7176a-6ae8-4127-9ea7-1ed0ef428205
nom: Rave
localisation:
United States
['US']
---------------
mbid:  2512e824-d092-474d-ac14-346b318fa8b1
nom: Laurie Records
localisation:
United States
['US']
dates {'begin': '1958'}
---------------
mbid:  669367fb-13e9-4fc9-a8d7-82fd4a173fdc
nom: Nightowl Records
localisation:
United States
['US']
---------------
mbid:  14b8dbbc-aba8-4a74-a41c-50315804ed9d
nom: Kings of Shortwaving
localisation:
Estonia
['EE']
---------------
mbid:  651d0d55-eee0-41d3-a28a-bc30a5a8dd74
nom: PeeBee Records
---------------
mbid:  85d397d0-b35c-4ee6-81ef-3fb4b0c2d70c
nom: American Gramaphone, LLC
localisation:
Omaha
############# {'sort-name': 'Omaha', 'id': '7968b302-75a6-4456-a09e-7bf7ac13293a', 'name': 'Omaha'}
EST PROPRIETAIRE DE: 
9e66ff44-4255-48ef-bde6-46e94d687120
American Gramaphone
TROUVE!!!!!!!!!!!! :)
---------------
mb

mbid:  de8af22d-20f3-47d8-8d58-0fd707ae4149
nom: Messidor
localisation:
Germany
['DE']
dates {'ended': 'true', 'begin': '1980', 'end': '1999'}
EST PROPRIETAIRE DE: 
17c46b1a-8842-4d83-b572-4f5290cce51b
Third
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  d9d02798-c3c7-4099-b5eb-96651dce563a
nom: Drowned Productions
---------------
mbid:  3610ab5d-2ecf-4efe-8e7a-9080d26e0b77
nom: Mass Appeal Entertainment
localisation:
United States
['US']
dates {'begin': '1995'}
---------------
mbid:  99766aaa-5bf3-4dd0-93a6-b9ed5955e4f3
nom: Peer-Southern-Productions GmbH
---------------
mbid:  0dcf6dac-f661-4878-94f5-49cfaec73abb
nom: We Be Records
localisation:
United Kingdom
['GB']
dates {'begin': '2008'}
---------------
mbid:  1262d33c-053e-4ddf-b732-146012a058f8
nom: K‐tel
localisation:
Winnipeg
############# {'sort-name': 'Winnipeg', 'id': '35307acf-aba0-4ca7-9df6-b9398d873a8f', 'name': 'Winnipeg'}
dates {'begin': '1968'}
EST PROPRIETAIRE DE: 
0948686f-e426-4295-906a-0034e46f00b9
Arrival Records
T

localisation:
United Kingdom
['GB']
dates {'begin': '2005'}
APPARTIENT A
729dc24f-95cc-4e80-a7b0-9e738827de9f
Plastic Fantastic Label Management
TROUVE!!!!!!!!!!!! :)
APPARTIENT A
9f4c14a6-1c3c-4cea-b646-fcf01b4d3fa8
Armada Music B.V.
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  9cfd88ee-b6ad-44e5-89d5-087135e93ffe
nom: Phontastic
localisation:
United States
['US']
---------------
mbid:  50edc910-29be-4baa-b8f2-c7b965c6686e
nom: Eager Beaver Records
---------------
mbid:  fc6c268e-68e6-49b5-b04a-96d5d3d9c6a0
nom: Excelsior Recordings
localisation:
Netherlands
['NL']
dates {'begin': '1996'}
EST PROPRIETAIRE DE: 
70ded4d5-410f-4854-8fc3-b14ca04eb0d3
Re
---------------
mbid:  457cce2d-0582-4c3d-9022-7cae9a7f42aa
nom: Gentle Threat
---------------
mbid:  e29d2e51-07ea-4346-b216-95b39c48a508
nom: R Radical Records
localisation:
United States
['US']
---------------
mbid:  616ccd6b-d707-4e0a-acbf-be40e13cec9e
nom: Parsifal
localisation:
Belgium
['BE']
dates {'begin': '1974'}
EST PROPRIETAIRE 

United States
['US']
---------------
mbid:  57a064a8-b99c-4add-bb66-8e95c80ca2fe
nom: Dacru Records
localisation:
Ghent
############# {'sort-name': 'Ghent', 'id': '45125c6a-db29-4300-bd26-9ff9ed24a3e7', 'name': 'Ghent'}
dates {'begin': '2006'}
---------------
mbid:  35432b31-52fa-42fc-8fae-0eeccdd5d3c1
nom: Driftin' Camel Jock Records
localisation:
United States
['US']
---------------
mbid:  cb08b054-0a3a-48c6-9d7f-bb56028cc46d
nom: The Agriculture
localisation:
United States
['US']
---------------
mbid:  95c42f6a-00e4-4709-8e57-f191453270c5
nom: Adventure Records
localisation:
Sweden
['SE']
---------------
mbid:  c185c05a-bf15-405b-b06c-19a2010b205a
nom: Culture Factory
localisation:
France
['FR']
---------------
mbid:  3cceb2e7-1378-42b5-9551-3a0c832e47eb
nom: International Dee Jay Gigolo Records and Publishing GmbH & Co. KG
localisation:
Berlin
['DE-BE']
EST PROPRIETAIRE DE: 
a1011157-4378-4dee-a6ed-0171e0b0227c
International Deejay Gigolo Records
TROUVE!!!!!!!!!!!! :)
-------------

localisation:
Netherlands
['NL']
---------------
mbid:  ef0c7459-d94f-4624-993f-55fcdc0eb807
nom: Famoso
---------------
mbid:  66b9c908-12b9-449e-b793-5e343d574d0f
nom: Piet Roelen Productions
---------------
mbid:  6c70b2ce-eb55-4af9-a2a9-c00c27b08955
nom: Flying Tigers Music
---------------
mbid:  725a7edb-7b12-43d1-bcea-22bfe2276af5
nom: Unique Uncut
localisation:
United Kingdom
['GB']
---------------
mbid:  1b451999-1542-4d7a-b0b4-4430ebc05e0d
nom: Mediatone
localisation:
Russia
['RU']
---------------
mbid:  466bed12-3c9d-4065-bcc1-bc948b20a2bc
nom: Nublu Records
localisation:
United States
['US']
dates {'begin': '2005'}
APPARTIENT A
159ec4fd-a29f-4dd8-931d-718c51f6735e
Discograph
TROUVE!!!!!!!!!!!! :)
APPARTIENT A
4435d87d-4062-4fb8-b4c7-6e25a239cf26
EMI Music Turkey
TROUVE!!!!!!!!!!!! :)
APPARTIENT A
45cdb379-4f4d-41ee-860c-db6e395a2c75
Redeye
TROUVE!!!!!!!!!!!! :)
---------------
mbid:  02bdcb43-666b-4ca9-ba70-467ef0258fc5
nom: Black Dragon Records
localisation:
Paris
['FR-75']

In [45]:
with open("missing_nodes.obj", 'rb') as handle:
                        missing_nodes= pickle.load(handle)

In [ ]:
#ON VEUT UN DEGRE DE FILIATION VERS LE BAS ET LE MAX VERS LE HAUT

In [52]:
extra_labels_dict={}
print len(missing_nodes)
print len(set(missing_nodes))
for label in set(missing_nodes):
    
    extra_labels_dict[label] = musicbrainzngs.get_label_by_id(label, includes=["aliases", "annotation", "area-rels", "label-rels", "place-rels"])
    print len(extra_labels_dict)
    print extra_labels_dict[label]["label"]["name"]
    if "label-relation-list" in extra_labels_dict[label]["label"]:
        #print "relations", labels_aliases[lab]["label"]["label-relation-list"]
        for relation in extra_labels_dict[label]["label"]["label-relation-list"]:
            #print "relation",relation
            locker=0

            if "direction" in relation: 
                if relation["direction"] == 'backward': print "APPARTIENT A"
                else:
                        print relation["direction"]
            else:
                print "EST PROPRIETAIRE DE: "
                locker=1
            print relation['target']
            print relation['label']['name']
            cnt=0
            for target, data in labels_aliases.iteritems():
                #print "DATA",data
                #print "TARGET",target
                if target == relation['target'] :
                    print "TROUVE!!!!!!!!!!!! :)"
                    locker=1
                    cnt+=1
                    break
            if cnt == 0 :
                    for  node in set(missing_nodes):
                        if  node ==  relation['target']:
                            print "TROUVE DE JUSTESSE!!!!!!!!!!!! :X",node
                            locker=1
                            break
                            
                    
            if locker == 0:
                
                print "ABSENT, ON AJOUTE A LA LISTE DES MANQUANTS"
                missing_nodes.append(relation['target'])
                print len(missing_nodes)
#print extra_labels_dict
with open('extra_labels_dict.obj', 'wb') as handle:
    pickle.dump(extra_labels_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)
    

1
1
1
Capitol Music Company
EST PROPRIETAIRE DE: 
053528f5-9570-4b50-9a54-b440526e5e99
Capitol Records
TROUVE!!!!!!!!!!!! :)
EST PROPRIETAIRE DE: 
2932d3a4-7bcc-48ef-832a-032b3c8ffc2b
Parlophone Records TOKYO
EST PROPRIETAIRE DE: 
5b0b1350-b302-4ec9-a9fc-4a3c553e4936
Awake Sounds
APPARTIENT A
753a8b77-b328-4618-addb-4d8243c0bf5e
EMI Music Japan Inc.
TROUVE!!!!!!!!!!!! :)
APPARTIENT A
d5a60c75-26e2-4363-a5db-58c12b578cd5
東芝EMI 株式会社
TROUVE!!!!!!!!!!!! :)


In [53]:
print str(extra_labels_dict)[:1000]
print str(labels_aliases)[:1000]
print len(extra_labels_dict)
print len(labels_aliases)
labels_aliases.update(extra_labels_dict)
print len(labels_aliases)

{'46b3f9e4-cb13-46c9-bd80-6682bdb3b853': {'label': {'name': 'Capitol Music Company', 'area': {'sort-name': 'Japan', 'iso-3166-1-code-list': ['JP'], 'id': '2db42837-c832-3c27-b4a3-08198f75693c', 'name': 'Japan'}, 'country': 'JP', 'disambiguation': 'division of EMI Music Japan', 'life-span': {'ended': 'true', 'end': '2008-12'}, 'alias-count': 2, 'sort-name': 'Capitol Music Company', 'alias-list': [{'sort-name': 'Capitol Music co.', 'alias': 'Capitol Music co.'}, {'sort-name': u'\u30ad\u30e3\u30d4\u30c8\u30eb \u30df\u30e5\u30fc\u30b8\u30c3\u30af', 'alias': u'\u30ad\u30e3\u30d4\u30c8\u30eb \u30df\u30e5\u30fc\u30b8\u30c3\u30af'}], 'annotation': {'text': "Capitol Music Company is a '''Japanese company'''.  Domestic Japanese releases used Japanese labels, such as [http://musicbrainz.org/label/053528f5-9570-4b50-9a54-b440526e5e99|a variant of the Capitol Records imprint] or the [label:5b0b1350-b302-4ec9-a9fc-4a3c553e4936|Awake Sounds] label. (This is not the same logo that the company's websit

In [54]:
with open('extra_labels_dictTOTAL.obj', 'wb') as handle:
    pickle.dump(extra_labels_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [11]:
for lab in labels_aliases:
    print "---------------"
    print lab
    print labels_aliases[lab]["label"]

---------------
781c73fd-71d0-4309-b9bb-a3036ffc705c
{'name': 'The Spew Records', 'area': {'sort-name': 'Italy', 'id': 'c6500277-9a3d-349b-bf30-41afdbf42add', 'name': 'Italy', 'iso-3166-1-code-list': ['IT']}, 'country': 'IT', 'life-span': {'begin': '2000'}, 'id': '781c73fd-71d0-4309-b9bb-a3036ffc705c', 'sort-name': 'The Spew Records', 'alias-list': [{'sort-name': 'Spew Records, The', 'alias': 'The Spew Records'}], 'type': 'Original Production', 'alias-count': 1}
---------------
a7d455f1-93f6-4bb7-a9cf-e4514efd7e02
{'name': 'Ulftone Music', 'area': {'sort-name': 'Germany', 'id': '85752fda-13c4-31a3-bee5-0e5cb1f51dad', 'name': 'Germany', 'iso-3166-1-code-list': ['DE']}, 'country': 'DE', 'sort-name': 'Ulftone Music', 'label-code': '1033', 'type': 'Original Production', 'id': 'a7d455f1-93f6-4bb7-a9cf-e4514efd7e02'}
---------------
c3da866a-1ed0-4d10-96e0-d6b5b80a50a0
{'name': 'Label "X"', 'area': {'sort-name': 'Australia', 'id': '106e0bec-b638-3b37-b731-f53d507dc00e', 'name': 'Australia', 

2c6bbfc8-e062-4cab-b0cb-f208afbef9f7
{'sort-name': 'Heaven & Earth Magic Recording Co.', 'area': {'sort-name': 'United States', 'id': '489ce91b-6658-3307-9877-795b68554c98', 'name': 'United States', 'iso-3166-1-code-list': ['US']}, 'id': '2c6bbfc8-e062-4cab-b0cb-f208afbef9f7', 'name': 'Heaven & Earth Magic Recording Co.', 'country': 'US'}
---------------
beae8d7a-fd6f-4c37-8b83-ab74329d928a
{'name': 'Grande lontra', 'area': {'sort-name': 'Italy', 'id': 'c6500277-9a3d-349b-bf30-41afdbf42add', 'name': 'Italy', 'iso-3166-1-code-list': ['IT']}, 'country': 'IT', 'sort-name': 'Grande lontra', 'label-code': '21564', 'id': 'beae8d7a-fd6f-4c37-8b83-ab74329d928a'}
---------------
0912a668-581e-4643-9a38-195e65dcbce5
{'name': 'City Centre Offices', 'area': {'sort-name': 'Germany', 'id': '85752fda-13c4-31a3-bee5-0e5cb1f51dad', 'name': 'Germany', 'iso-3166-1-code-list': ['DE']}, 'country': 'DE', 'life-span': {'begin': '1999'}, 'sort-name': 'City Centre Offices', 'label-code': '9554', 'label-relatio

16eaa3da-4fa8-4c1f-bc0d-b0246363f7db
{'sort-name': 'Wanted Man Music', 'type': 'Bootleg Production', 'id': '16eaa3da-4fa8-4c1f-bc0d-b0246363f7db', 'name': 'Wanted Man Music'}
---------------
a53906c5-8bc7-4213-8bd7-4a4c6c93faa2
{'name': 'Victor Records', 'area': {'sort-name': 'United States', 'id': '489ce91b-6658-3307-9877-795b68554c98', 'name': 'United States', 'iso-3166-1-code-list': ['US']}, 'country': 'US', 'disambiguation': 'primary imprint of the Victor Talking Machine Company', 'life-span': {'ended': 'true', 'begin': '1901-10-03', 'end': '1929'}, 'sort-name': 'Victor Records', 'alias-list': [{'sort-name': 'Victor Talking Machine Company', 'alias': 'Victor Talking Machine Company'}], 'id': 'a53906c5-8bc7-4213-8bd7-4a4c6c93faa2', 'annotation': {'text': 'One of the oldest labels, Victor also is remarkable for it never produced cylinders but directly bet on discs.\nAs such, it was involved in the early lawsuits from which it eventually emerged as a winner, buying both Zonophone and 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.
